# Green and Red Candle Project
## Coded by Victor Zheng & Supervised under Mohammed Hasan

## Progress
##### 04-17-2021: Debugged last index dateTimeMaxHTP for why it was (0,0,0)
##### 04-18-2021: Worked on getting dateTimeMinLTP - the minimum LTP for a paritcular row in dateTimeMaxHTP

In [1]:
import pandas as pd
import numpy as np
import math
#df = pd.read_csv('Jan 2020 - Dec 2020 merged SPY - Copy.csv')
df = pd.read_csv('Even-smaller-dataframe.csv')
df

Date TimeBarStart Ticker CallPut  Strike  ExpirationDate  \
0      20200304   9:30:00 AM    SPY       P   306.5        20200304   
1      20200304   9:30:00 AM    SPY       P   288.0        20200304   
2      20200304   9:30:00 AM    SPY       P   279.0        20200304   
3      20200304   9:30:00 AM    SPY       P   304.5        20200304   
4      20200304   9:30:00 AM    SPY       P   289.0        20200304   
...         ...          ...    ...     ...     ...             ...   
80348  20200311   4:14:00 PM    SPY       C   274.0        20200311   
80349  20200311   4:14:00 PM    SPY       C   271.0        20200311   
80350  20200311   4:14:00 PM    SPY       C   276.0        20200311   
80351  20200311   4:14:00 PM    SPY       C   282.0        20200311   
80352  20200311   4:14:00 PM    SPY       C   280.0        20200311   

       OpenTradePrice  HighTradePrice  LowTradePrice  CloseTradePrice  \
0                2.64            2.76           2.64             2.76   
1                0.04            0.06           0.03             0.03   
2                0.01            0.01           0.01             0.01   
3                1.70            1.70           1.62             1.62   
4                0.03            0.05           0.03             0.05   
...               ...             ...            ...              ...   
80348            1.06            1.11           1.02             1.05   
80349            3.75            3.75           3.75             3.75   
80350            0.27            0.28           0.17             0.25   
80351            0.01            0.01           0.01             0.01   
80352            0.02            0.02           0.02             0.02   

       UnderOpenBidPrice  UnderOpenAskPrice  UnderCloseBidPrice  \
0                 306.05             306.07              305.85   
1                 306.06             306.07              306.19   
2                 305.95             305.97              305.95   
3                 306.15             306.16              306.38   
4                 306.09             306.11              306.17   
...                  ...                ...                 ...   
80348             274.65             274.71              274.62   
80349             274.67             274.71              274.67   
80350             274.70             274.74              274.59   
80351             274.54             274.59              274.54   
80352             274.58             274.64              274.58   

       UnderCloseAskPrice    VWAP  Volume  TotalTrades  
0                  305.87  2.7000       2            2  
1                  306.20  0.0418      11            6  
2                  305.97  0.0100      25            1  
3                  306.40  1.6886       7            2  
4                  306.19  0.0389      36            4  
...                   ...     ...     ...          ...  
80348              274.68  1.0830      23            7  
80349              274.71  3.7500       1            1  
80350              274.60  0.2406      17            8  
80351              274.59  0.0100       3            2  
80352              274.64  0.0200     100            1  

[80353 rows x 17 columns]

## Get minimum value for call/put between 9:46AM and the timecallmax for that day

In [11]:
#function that compares if time 1 is < time 2
def beforeTime(time1,time2):
    
    if len(time1) != 11:
        time1 = "0" + time1
    if len(time2) != 11:
        time2 = "0" + time2
    
    #check last 2 chars to see if AM or PM
    if time1[-2:] == "AM":
        t1IsAM = True
    else:
        t1IsAM = False
    if time2[-2:] == "AM":
        t2IsAM = True
    else:
        t2IsAM = False
    
    if t1IsAM and not t2IsAM:
        return True
    elif t1IsAM and t2IsAM:
        return True if time1 < time2 else False
    elif not t1IsAM and t2IsAM:
        return False
    else: #t1 is pm and t2 is pm
        return True if time1 < time2 else False

#sample test cases - expected TFFF
print(beforeTime("10:05:00 AM","3:59:00 PM"), beforeTime("10:05:00 PM","3:59:00 PM"), beforeTime("10:05:00 AM","3:59:00 AM"),beforeTime("10:05:00 PM","3:59:00 AM"))

def afterTime(time1,time2):
    if time1 == time2:
        return False
    return not beforeTime(time1,time2)

True False False False


### Starting price difference - green (increase) and red (decrease) indicators for the first 5 mins of each date

In [3]:
dateTimeCandleSP = [] #(date,time,color,StrikePrice,StockPrice)
date = df.iloc[0]["Date"]
openPrice = df.iloc[0]["UnderOpenAskPrice"]
skipDate = False
#indices: 0=Date, 1=TimeBarStart, 13= UnderCloseAskPrice, 11=UnderOpenAskPrice
for index,row in df.iterrows():
    #we are looking for the UnderOpenAskPrice(UOAP) at 9:30:00 AM (the first time it occurs) 
    #we are looking for the UnderOpenAskPrice (UOAP) at 9:36:00 AM (the last time it occurs)
    #then we subtract the 9:35:00 AM time by the 9:30:00 AM time
    
    if date == row[0]:
        if skipDate:
            continue
        #lastPrice = row["UnderCloseAskPrice"]
        prevRow = row
        #if time is past 9:35AM, then use the latest 9:35AM (if it doesn't exist, then use the current row's time)
        time = row[1]
        if not beforeTime(time,"9:36:00 AM"):
            #calculate starting price difference
            
            #if 9:35 exists
            if prevRow[1] == "9:35:00 AM":
                #we take the UnderCloseAskPrice
                lastPrice = prevRow[13]
            else:
                #if 9:35 doesn't exist
                #if 9:36 exists, then take the open price, otherwise skip this date
                if time == "9:36:00 AM":
                    lastPrice = row[11]
                else:
                    skipDate = True
                    continue
            diff = lastPrice - openPrice
            if math.isnan(diff):
                #either openPrice or lastPrice doesn't exist
                skipDate = True
                continue
            #print("date={},lastPrice={}".format(date,lastPrice))
            if diff >= 0:
                #green start
                dateTimeCandleSP.append((date,time,"GREEN",math.ceil(lastPrice),lastPrice))
            else:
                dateTimeCandleSP.append((date,time,"RED",math.floor(lastPrice),lastPrice))
            skipDate = True
    else:
        #we found new date, get the green/red bar for the previous date, reinitialize some variables
        date = row[0]
        openPrice = row[11]
        skipDate = False

In [4]:
#(date,time,color,StrikePrice,StockPrice)
dateTimeCandleSP

[(20200304, '9:36:00 AM', 'RED', 305, 305.36),
 (20200306, '9:36:00 AM', 'GREEN', 294, 293.8),
 (20200311, '9:36:00 AM', 'GREEN', 282, 281.13)]

In [5]:
dtcspIdx = 0
dfStartIdx = 0
dateWithOTP = [] #(date, time, CallPut, SP, OTP)
for dtcsp in dateTimeCandleSP:
    #print("dateWithOTP: {}".format(dateWithOTP))
    date, time, color, strikeP = dtcsp[0],dtcsp[1],dtcsp[2], dtcsp[3]
    for index,row in df.iloc[dfStartIdx:].iterrows():
        if color == "GREEN":
            #This is call, get OpenTradePrice(OTP) at 9:36AM
            #Match Date, Time, Call=C, StrikePrice
            if row[0] == date and row[1] == time and row[3] == "C" and row[4] == strikeP:
                dateWithOTP.append((date,time,"C",strikeP,row[6]))
                #update for next iteration of dtcsp
                dfStartIdx = index + 1
                break
        else:
            #This is put, get OpenTradePrice(OTP) at 9:36AM
            #Match Date, Time, Call=P, StrikePrice
            if row[0] == date and row[1] == time and row[3] == "P" and row[4] == strikeP:
                dateWithOTP.append((date,time,"P",strikeP,row[6]))
                #update for next iteration of dtcsp
                dfStartIdx = index + 1
                break

#if the candle is green then we want to buy a call
#if call then you look for the UnderOpenAskPrice at 9:36:00 AM and round that up to next whole number, this gets the Call_SP
#then we look for the Call_SP and see what the OpenTradePrice is at 9:36:00 AM


#if the candle is red then we want to buy a put
#if put then you look for the UnderOpenAskPrice at 9:36:00 AM and round that down to next whole number, this gets the Put_SP
#then we look for the Put_SP and see what the OpenTradePrice is at 9:36:00 AM

In [6]:
#(date, time, CallPut, SP, OTP)
print("(date, time,CallPut, SP, OTP)")
dateWithOTP

(date, time,CallPut, SP, OTP)


[(20200304, '9:36:00 AM', 'P', 305, 2.26),
 (20200306, '9:36:00 AM', 'C', 294, 2.87),
 (20200311, '9:36:00 AM', 'C', 282, 3.24)]

#### For each date,SP,CallPut in dateWithOTP, find the maximum of the hightradeprice and time (b/w 9:37:00 AM to 3:59:00 PM

In [39]:
dfStartIdx = 0
#Date	TimeBarStart	Ticker	CallPut	Strike	ExpirationDate	OpenTradePrice	HighTradePrice	LowTradePrice	CloseTradePrice	
dateTimeMaxHTP = [(0,0,0,0,0) for _ in range(len(dateWithOTP))] #[date,time,CallPut,SP,maxHTP]
prevDate = dateWithOTP[0][0]
N = len(df)
curDfLen = N
for dOTPidx, (date,_,CallPut,sp,_) in enumerate(dateWithOTP):
    #print("Checking for date={},CallPut={},sp={}".format(date,CallPut,sp))
    maxHTP = -1
    doSameDate = False
    for index,row in df.iloc[dfStartIdx:].iterrows():
        #print("index,dfStartIdx,N-dfStartIdx-1: {},{},{}".format(index,dfStartIdx,N-dfStartIdx-1))
        #print("htp={},maxHTP={},time={}".format(row[7],maxHTP,row[1]))
        if index == N-1: #index == N - dfStartIdx - 2:
            #needed this one here to check for end index, which can contain time inside the timeframe we want
            #print("if4.1-----------------------------------------")
            #case 1 - we're done with prev date
            dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,CallPut,sp,maxHTP)

            #initialize variables for next iteration of dateWithOTP
            dfStartIdx = index + 1
            prevDate = row[0]
            maxHTP = -1
            break
            
        if beforeTime(row[1],"9:37:00 AM") or afterTime(row[1],"3:59:00 PM"):
            if index == N-1: #index == N - dfStartIdx - 2:
                #need this one here again because the last index may have time that is outside of timeframe
                #print("if4.1-----------------------------------------")
                #case 1 - we're done with prev date
                dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,CallPut,sp,maxHTP)
            
                #initialize variables for next iteration of dateWithOTP
                dfStartIdx = index + 1
                prevDate = row[0]
                maxHTP = -1
                break
            continue
        elif date == row[0] and CallPut == row[3] and sp == row[4]:
            #print("if1")
            #print("row: {}".format(list(row)))
            #Check if there's a new max HTP
            #print("htp={},maxHTP={},time={}".format(row[7],maxHTP,row[1]))
            if row[7] > maxHTP:
                #print("if2")
                #print("update for maxHTP: {}".format(row[7]))
                maxHTP = row[7]
                maxHTPTime = row[1]
        elif date != row[0]:
            #print("if3")
            #date doesn't match, so we're done searching for previous date OR this date has no value in df
            if maxHTP != -1: #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMaxHTP  
                #print("if4")
                #case 1 - we're done with prev date
                dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,CallPut,sp,maxHTP)
            
                #initialize variables for next iteration of dateWithOTP
                dfStartIdx = index + 1
                prevDate = row[0]
                maxHTP = -1
                break
            elif index == N-1: #index == N - dfStartIdx - 2:
                #print("if4.1-----------------------------------------")
                #case 1 - we're done with prev date
                dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,CallPut,sp,maxHTP)
            
                #initialize variables for next iteration of dateWithOTP
                dfStartIdx = index + 1
                prevDate = row[0]
                maxHTP = -1
                break
            else:
                #print('if5')
                #Case 2 - date has no value in df, so doesn't exist in dateWithOTP
                #keep iterating until we past this date and until we found the date that matches dateWithOTP
                dfStartIdx = index + 1
                #print("dfStartIdx: {}".format(dfStartIdx))
                for indexb,rowb in df.iloc[dfStartIdx:].iterrows():
                    if rowb[0] == date:
                        #print("if6")
                        prevDate = rowb[0]
                        dfStartIdx = indexb
                        doSameDate = True #found matching date so now iterate from that as startIdx to cover it instead of using current for loop
                        break
                if doSameDate:
                    #print("if7")
                    break
            

    if doSameDate:
        #print("if7.2")
        for index,row in df.iloc[dfStartIdx:].iterrows():
            #print("index,dfStartIdx,N-dfStartIdx-1: {},{},{}".format(index,dfStartIdx,N-dfStartIdx-1))
            if index == N-1: #N - dfStartIdx - 2: # 80352 - 41175 # - 1
                    #print("if11")
                    #reached the last index in df, so update for maxHTP
                    #case 1 - we're done with prev date
                    dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,CallPut,sp,maxHTP)

                    #initialize variables for next iteration of dateWithOTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    maxHTP = -1
                    break
                    
            if beforeTime(row[1],"9:37:00 AM") or afterTime(row[1],"3:59:00 PM"):
                if index == N-1: #N - dfStartIdx - 2: # 80352 - 41175 # - 1
                    #print("if11")
                    #reached the last index in df, so update for maxHTP
                    #case 1 - we're done with prev date
                    dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,CallPut,sp,maxHTP)

                    #initialize variables for next iteration of dateWithOTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    maxHTP = -1
                    break
                continue
            elif date == row[0] and CallPut == row[3] and sp == row[4]:
                #print("if8")
                #print("row: {}".format(list(row)))
                #Check if there's a new max HTP
                #print("htp={},maxHTP={},time={}".format(row[7],maxHTP,row[1]))
                if row[7] > maxHTP:
                    #print("if9")
                    #print("update for maxHTP: {}".format(row[7]))
                    maxHTP = row[7]
                    maxHTPTime = row[1]
            elif date != row[0]:
                #date doesn't match, so we're done searching for previous date OR this date has no value in df
                #print("if10")
                if maxHTP != -1: #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMaxHTP 
                    #case 1 - we're done with prev date
                    dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,CallPut,sp,maxHTP)

                    #initialize variables for next iteration of dateWithOTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    maxHTP = -1
                    break
            

In [40]:
dateTimeMaxHTP

[(20200304, '9:58:00 AM', 'P', 305, 3.52),
 (20200306, '10:51:00 AM', 'C', 294, 5.15),
 (20200311, '9:37:00 AM', 'C', 282, 3.5)]

#### find the minimum of the option (LowTradePrice) from 9:37:00 AM to the maxHTP time
#### if the max time occurs at 9:37:00 AM then find the minimum LowTradePrice of the option from 9:37:00 AM to the end of the day

In [41]:
dfStartIdx = 0
#Date	TimeBarStart	Ticker	CallPut	Strike	ExpirationDate	OpenTradePrice	HighTradePrice	LowTradePrice	CloseTradePrice	
dateTimeMinLTP = [(0,0,0,0,0) for _ in range(len(dateTimeMaxHTP))] #[date,time,CallPut,SP,minLTP]
prevDate = dateTimeMaxHTP[0][0]
N = len(df)
curDfLen = N
for dTMidx, (date,maxHTPTime,CallPut,sp,_) in enumerate(dateTimeMaxHTP):
    print("Checking for date={},maxHTPTime={},CallPut={},sp={}".format(date,maxHTPTime,CallPut,sp))
    minLTP = float("inf")
    doSameDate = False
    
    if maxHTPTime == "9:37:00 AM":
        #if the max time occurs at 9:37:00 AM then find the minimum LowTradePrice of the option from 9:37:00 AM to the end of the day
        for index,row in df.iloc[dfStartIdx:].iterrows():
            print("index,dfStartIdx,N-dfStartIdx-1: {},{},{}".format(index,dfStartIdx,N-dfStartIdx-1))
            print("htp={},minLTP={},time={}".format(row[8],minLTP,row[1]))
            if index == N-1: #index == N - dfStartIdx - 2:
                #case 1 - we're done with prev date
                print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                #initialize variables for next iteration of dateTimeMaxHTP
                dfStartIdx = index + 1
                prevDate = row[0]
                minLTP = float("inf")
                break

            #want 9:37AM to end of day
            #otherwise toss out this row
            if beforeTime(row[1],"9:37:00 AM") or afterTime(row[1],"3:59:00 PM"):
                if index == N-1: #index == N - dfStartIdx - 2:
                    #case 1 - we're done with prev date
                    print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                    dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                    #initialize variables for next iteration of dateTimeMaxHTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    minLTP = float("inf")
                    break
                continue
            elif date == row[0] and CallPut == row[3] and sp == row[4]:
                print("row: {}".format(list(row)))
                #Check if there's a new max HTP
                print("htp={},minLTP={},time={}".format(row[8],minLTP,row[1]))
                if row[8] < minLTP:
                    print("update for minLTP: {}".format(row[8]))
                    minLTP = row[8]
                    minLTPTime = row[1]
            elif date != row[0]:
                #date doesn't match, so we're done searching for previous date OR this date has no value in df
                if minLTP != float("inf"): #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMinLTP  
                    #case 1 - we're done with prev date
                    print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                    dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                    #initialize variables for next iteration of dateTimeMaxHTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    minLTP = float("inf")
                    break
                elif index == N-1: #index == N - dfStartIdx - 2:
                    #case 1 - we're done with prev date
                    print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                    dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                    #initialize variables for next iteration of dateTimeMaxHTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    minLTP = float("inf")
                    break
                else:
                    print('if5')
                    #Case 2 - date has no value in df, so doesn't exist in dateTimeMaxHTP
                    #keep iterating until we past this date and until we found the date that matches dateTimeMaxHTP
                    dfStartIdx = index + 1
                    print("dfStartIdx: {}".format(dfStartIdx))
                    for indexb,rowb in df.iloc[dfStartIdx:].iterrows():
                        if rowb[0] == date:
                            prevDate = rowb[0]
                            dfStartIdx = indexb
                            doSameDate = True #found matching date so now iterate from that as startIdx to cover it instead of using current for loop
                            break
                    if doSameDate:
                        break
            

        if doSameDate:
            for index,row in df.iloc[dfStartIdx:].iterrows():
                print("index,dfStartIdx,N-dfStartIdx-1: {},{},{}".format(index,dfStartIdx,N-dfStartIdx-1))
                if minLTP != float("inf"): #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMinLTP  
                    #case 1 - we're done with prev date
                    print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                    dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                    #initialize variables for next iteration of dateTimeMaxHTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    minLTP = float("inf")
                    break

                #want 9:37AM to end of day
                #otherwise toss out this row
                if beforeTime(row[1],"9:37:00 AM") or afterTime(row[1],"3:59:00 PM"):
                    if index == N-1: #N - dfStartIdx - 2: # 80352 - 41175 # - 1
                        #reached the last index in df, so update for minLTP
                        #case 1 - we're done with prev date
                        print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                        dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                        #initialize variables for next iteration of dateTimeMaxHTP
                        dfStartIdx = index + 1
                        prevDate = row[0]
                        minLTP = float("inf")
                        break
                    continue
                elif date == row[0] and CallPut == row[3] and sp == row[4]:
                    print("row: {}".format(list(row)))
                    #Check if there's a new max HTP
                    print("htp={},minLTP={},time={}".format(row[8],minLTP,row[1]))
                    if row[8] < minLTP:
                        print("update for minLTP: {}".format(row[8]))
                        minLTP = row[8]
                        minLTPTime = row[1]
                elif date != row[0]:
                    #date doesn't match, so we're done searching for previous date OR this date has no value in df
                    if minLTP != float("inf"): #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMinLTP 
                        #case 1 - we're done with prev date
                        print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                        dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                        #initialize variables for next iteration of dateTimeMaxHTP
                        dfStartIdx = index + 1
                        prevDate = row[0]
                        minLTP = float("inf")
                        break
    else:
        #max occurs after 9:37AM - find the minimum of the option (LowTradePrice) from 9:37:00 AM to the max HTP time
        for index,row in df.iloc[dfStartIdx:].iterrows():
            print("index,dfStartIdx,N-dfStartIdx-1: {},{},{}".format(index,dfStartIdx,N-dfStartIdx-1))
            print("htp={},minLTP={},time={}".format(row[8],minLTP,row[1]))
            if index == N-1: #index == N - dfStartIdx - 2:
                #case 1 - we're done with prev date
                print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                #initialize variables for next iteration of dateTimeMaxHTP
                dfStartIdx = index + 1
                prevDate = row[0]
                minLTP = float("inf")
                break

            #want 9:37AM to maxHTP time
            #toss out others
            if beforeTime(row[1],"9:37:00 AM") or afterTime(row[1],maxHTPTime):
                if index == N-1: #index == N - dfStartIdx - 2:
                    #case 1 - we're done with prev date
                    print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                    dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                    #initialize variables for next iteration of dateTimeMaxHTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    minLTP = float("inf")
                    break
                continue
            elif date == row[0] and CallPut == row[3] and sp == row[4]:
                print("row: {}".format(list(row)))
                #Check if there's a new max HTP
                print("htp={},minLTP={},time={}".format(row[8],minLTP,row[1]))
                if row[8] < minLTP:
                    print("update for minLTP: {}".format(row[8]))
                    minLTP = row[8]
                    minLTPTime = row[1]
            elif date != row[0]:
                #date doesn't match, so we're done searching for previous date OR this date has no value in df
                if minLTP != float("inf"): #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMinLTP  
                    #case 1 - we're done with prev date
                    print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                    dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                    #initialize variables for next iteration of dateTimeMaxHTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    minLTP = float("inf")
                    break
                elif index == N-1: #index == N - dfStartIdx - 2:
                    #case 1 - we're done with prev date
                    print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                    dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                    #initialize variables for next iteration of dateTimeMaxHTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    minLTP = float("inf")
                    break
                else:
                    print('if5')
                    #Case 2 - date has no value in df, so doesn't exist in dateTimeMaxHTP
                    #keep iterating until we past this date and until we found the date that matches dateTimeMaxHTP
                    dfStartIdx = index + 1
                    print("dfStartIdx: {}".format(dfStartIdx))
                    for indexb,rowb in df.iloc[dfStartIdx:].iterrows():
                        if rowb[0] == date:
                            prevDate = rowb[0]
                            dfStartIdx = indexb
                            doSameDate = True #found matching date so now iterate from that as startIdx to cover it instead of using current for loop
                            break
                    if doSameDate:
                        break
            

            if doSameDate:
                for index,row in df.iloc[dfStartIdx:].iterrows():
                    print("index,dfStartIdx,N-dfStartIdx-1: {},{},{}".format(index,dfStartIdx,N-dfStartIdx-1))
                    if minLTP != float("inf"): #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMinLTP  
                        #case 1 - we're done with prev date
                        print("prevDate={},CallPut={},sp={},minLTP={}".format(prevDate,CallPut,sp,minLTP))
                        print("prevDate={},minLTPTime={},CallPut={},sp={},minLTP={}".format(prevDate,minLTPTime,CallPut,sp,minLTP))
                        dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                        #initialize variables for next iteration of dateTimeMaxHTP
                        dfStartIdx = index + 1
                        prevDate = row[0]
                        minLTP = float("inf")
                        break

                    if beforeTime(row[1],"9:37:00 AM") or afterTime(row[1],maxHTPTime):
                        if index == N-1: #N - dfStartIdx - 2: # 80352 - 41175 # - 1
                            #reached the last index in df, so update for minLTP
                            #case 1 - we're done with prev date
                            dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                            #initialize variables for next iteration of dateTimeMaxHTP
                            dfStartIdx = index + 1
                            prevDate = row[0]
                            minLTP = float("inf")
                            break
                        continue
                    elif date == row[0] and CallPut == row[3] and sp == row[4]:
                        print("row: {}".format(list(row)))
                        #Check if there's a new max HTP
                        print("htp={},minLTP={},time={}".format(row[8],minLTP,row[1]))
                        if row[8] < minLTP:
                            print("update for minLTP: {}".format(row[8]))
                            minLTP = row[8]
                            minLTPTime = row[1]
                    elif date != row[0]:
                        #date doesn't match, so we're done searching for previous date OR this date has no value in df
                        if minLTP != float("inf"): #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMinLTP 
                            #case 1 - we're done with prev date
                            dateTimeMinLTP[dTMidx] = (prevDate,minLTPTime,CallPut,sp,minLTP)

                            #initialize variables for next iteration of dateTimeMaxHTP
                            dfStartIdx = index + 1
                            prevDate = row[0]
                            minLTP = float("inf")
                            break

Checking for date=20200304,maxHTPTime=9:58:00 AM,CallPut=P,sp=305
index,dfStartIdx,N-dfStartIdx-1: 0,0,80352
htp=2.64,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1,0,80352
htp=0.03,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2,0,80352
htp=0.01,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 3,0,80352
htp=1.62,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 4,0,80352
htp=0.03,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 5,0,80352
htp=0.01,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 6,0,80352
htp=13.96,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 7,0,80352
htp=0.47,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 8,0,80352
htp=3.84,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 9,0,80352
htp=0.01,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 10,0,80352
htp=1.81,minLTP=inf,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 11,0,80352
htp=0.01,minLTP=inf

htp=6.09,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 724,0,80352
htp=0.33,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 725,0,80352
htp=4.54,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 726,0,80352
htp=2.71,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 727,0,80352
htp=1.44,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 728,0,80352
htp=0.05,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 729,0,80352
htp=4.9,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 730,0,80352
htp=3.99,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 731,0,80352
htp=14.3,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 732,0,80352
htp=0.08,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 733,0,80352
htp=3.5,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 734,0,80352
htp=1.24,minLTP=2.23,time=9:38:00 AM
index,dfStartIdx,N-dfStartIdx-1: 735,0,80352
htp=3.02,minLTP=2.

index,dfStartIdx,N-dfStartIdx-1: 1363,0,80352
htp=1.54,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1364,0,80352
htp=1.26,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1365,0,80352
htp=5.49,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1366,0,80352
htp=1.4,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1367,0,80352
htp=1.7,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1368,0,80352
htp=0.26,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1369,0,80352
htp=0.54,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1370,0,80352
htp=1.05,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1371,0,80352
htp=0.32,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1372,0,80352
htp=1.83,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1373,0,80352
htp=0.43,minLTP=2.22,time=9:48:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1374,0,80352
htp=2.34,minLTP=2.22,time=9:48:00 AM
index,

index,dfStartIdx,N-dfStartIdx-1: 1986,0,80352
htp=1.61,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1987,0,80352
htp=0.94,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1988,0,80352
htp=1.4,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1989,0,80352
htp=3.95,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1990,0,80352
htp=3.75,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1991,0,80352
htp=4.8,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1992,0,80352
htp=1.27,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1993,0,80352
htp=1.12,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1994,0,80352
htp=0.6,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1995,0,80352
htp=5.19,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1996,0,80352
htp=0.01,minLTP=2.22,time=9:58:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1997,0,80352
htp=0.16,minLTP=2.22,time=9:58:00 AM
index,d

index,dfStartIdx,N-dfStartIdx-1: 2649,0,80352
htp=0.04,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2650,0,80352
htp=2.05,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2651,0,80352
htp=4.19,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2652,0,80352
htp=2.27,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2653,0,80352
htp=1.35,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2654,0,80352
htp=0.15,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2655,0,80352
htp=0.69,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2656,0,80352
htp=0.95,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2657,0,80352
htp=9.96,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2658,0,80352
htp=0.24,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2659,0,80352
htp=6.52,minLTP=2.22,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2660,0,80352
htp=7.07,minLTP=2.22,time=10:0

...

htp=0.1,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39243,18655,61697
htp=2.66,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39244,18655,61697
htp=0.03,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39245,18655,61697
htp=0.07,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39246,18655,61697
htp=0.19,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39247,18655,61697
htp=2.0,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39248,18655,61697
htp=0.25,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39249,18655,61697
htp=1.35,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39250,18655,61697
htp=0.01,minLTP=1.9,time=3:34:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39251,18655,61697
htp=5.44,minLTP=1.9,time=3:35:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39252,18655,61697
htp=0.01,minLTP=1.9,time=3:35:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39253,18655,61697
htp=0.07,minLTP=1.9,time=3:35:00 PM
index,dfS

index,dfStartIdx,N-dfStartIdx-1: 39941,18655,61697
htp=44.89,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39942,18655,61697
htp=0.05,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39943,18655,61697
htp=0.02,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39944,18655,61697
htp=3.82,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39945,18655,61697
htp=0.02,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39946,18655,61697
htp=5.84,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39947,18655,61697
htp=0.11,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39948,18655,61697
htp=0.25,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39949,18655,61697
htp=0.52,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39950,18655,61697
htp=0.12,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39951,18655,61697
htp=10.1,minLTP=1.9,time=3:49:00 PM
index,dfStartIdx,N-dfStartIdx-1: 39952,186

index,dfStartIdx,N-dfStartIdx-1: 40751,18655,61697
htp=0.01,minLTP=1.9,time=4:02:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40752,18655,61697
htp=0.58,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40753,18655,61697
htp=0.23,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40754,18655,61697
htp=0.1,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40755,18655,61697
htp=0.13,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40756,18655,61697
htp=15.03,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40757,18655,61697
htp=7.92,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40758,18655,61697
htp=12.0,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40759,18655,61697
htp=1.18,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40760,18655,61697
htp=0.42,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40761,18655,61697
htp=2.88,minLTP=1.9,time=4:03:00 PM
index,dfStartIdx,N-dfStartIdx-1: 40762,1865

index,dfStartIdx,N-dfStartIdx-1: 41239,18655,61697
htp=2.33,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41240,18655,61697
htp=5.0,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41241,18655,61697
htp=0.21,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41242,18655,61697
htp=2.0,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41243,18655,61697
htp=11.25,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41244,18655,61697
htp=3.01,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41245,18655,61697
htp=0.01,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41246,18655,61697
htp=10.13,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41247,18655,61697
htp=5.0,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41248,18655,61697
htp=12.0,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41249,18655,61697
htp=0.65,minLTP=1.9,time=9:31:00 AM
index,dfStartIdx,N-dfStartIdx-1: 41250,18655

index,dfStartIdx,N-dfStartIdx-1: 61645,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61646,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61647,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61648,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61649,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61650,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61651,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61652,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61653,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61654,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61655,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61656,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61657,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61658,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61659,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61660,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61661,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61662,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 61663,61645,18707
index,dfStartIdx,N-dfStartIdx-1

In [42]:
[date,time,CallPut,SP,minLTP]
dateTimeMinLTP

[(20200304, '9:41:00 AM', 'P', 305, 2.22),
 (20200306, '9:53:00 AM', 'C', 294, 1.9),
 (20200311, '9:37:00 AM', 'C', 282, 3.32)]

In [ ]:
#Need to debug if maxHTPTime == "9:37:00 AM": case - it doesn't select the minLTP after maxtime, it selects the LTP at 9:37AM